# A quartic non-linear oscillator in phase space

Let us keep the algebra to a minimum and pick the potential

$$
V(x)=\tfrac 12 k x^{2}+g x^{4},
$$

with $k>0$ (harmonic part) and $g>0$ (hardening quartic term). Its
Hamiltonian reads

$$
H(x,p)=\frac{p^{2}}{2m}+V(x).
$$

Although the equations of motion are non‑linear, we could still
integrate them numerically using `scipy.integrate.solve_ivp`. However,
this goes out of the scope of this course, as we are interested in
linear ordinary differential equations and their matrix equivalents. To
restore linearity we have to take a step back and study **phase‑space
functions** rather than individual trajectories.

We can now construct the matrix operators for the Liouville equation
following **?@eq-central-difference-x**, **?@eq-central-difference-p**,
and **?@eq-liouville-matrix**. We can take advantage of the tools
provided by `scipy.sparse` to create the sparse matrices efficiently. We
start by importing the necessary libraries

In [2]:
import numpy as np
import matplotlib.pyplot as plt
import scipy as sp
import scipy.sparse as sparse
import functools as ft

# Define a Gaussian function, useful for initial conditions
def gaussian(x, mu, sigma):
    """Generate a Gaussian function."""
    norm_factor = 1 / (sigma * np.sqrt(2 * np.pi))
    return np.exp(-0.5 * ((x - mu) / sigma) ** 2) * norm_factor

And then we define the grid and the operators for the phase space:

In [3]:
N_x = 150 # Number of grid points in position space
N_px = 150 # Number of grid points in momentum space
x_bound = 5 # Position space boundary
px_bound = 5 # Momentum space boundary

# Identity matrices for the different dimensions
Ix = sparse.eye(N_x)
Ipx = sparse.eye(N_px)

x_list = np.linspace(-x_bound, x_bound, N_x)
px_list = np.linspace(-px_bound, px_bound, N_px)

dx = x_list[1] - x_list[0]
dpx = px_list[1] - px_list[0]

# Define the operators
x_op = sparse.diags(x_list)
px_op = sparse.diags(px_list)

# Use central differences for derivatives
d_x_op = sparse.diags([np.ones(N_x-1)/(2*dx), 
                -np.ones(N_x-1)/(2*dx)], offsets=[1, -1])
d_px_op = sparse.diags([np.ones(N_px-1)/(2*dpx),
                -np.ones(N_px-1)/(2*dpx)], offsets=[1, -1])

# Create the full operator for the 4D phase space
x = ft.reduce(sparse.kron, [Ipx, x_op]).todia()
px = ft.reduce(sparse.kron, [px_op, Ix]).todia()

d_x = ft.reduce(sparse.kron, [Ipx, d_x_op]).todia()
d_px = ft.reduce(sparse.kron, [d_px_op, Ix]).todia()

We can now compute the time evolution defined by **?@eq-liouville-ode**
by using the Euler method described in **?@sec-ode-euler-method**:

In [4]:
m = 0.5 # Mass of the particle
k = 2.0 # Spring constant
G = 0.15 # Nonlinear constant

dV_dx = k * x + 4 * G * x @ x @ x

# Liouville operator
L = dV_dx @ d_px - (px / m) @ d_x

t_list = np.linspace(0, 2, 100000)

# Initial state: we will use a Gaussian wave packet to avoid singularities
x_0 = gaussian(x_list, 1.0, np.sqrt(0.5))
p_0 = gaussian(px_list, 0.1, np.sqrt(0.5))
rho_0 = np.kron(p_0, x_0)

x_t = np.zeros(t_list.shape[0])
v_t = np.zeros(t_list.shape[0])
E_t = np.zeros(t_list.shape[0])

x_t[0] = rho_0.dot(x.dot(rho_0))
v_t[0] = rho_0.dot(px.dot(rho_0)) / m
E_t[0] = (0.5 * m * v_t[0]**2 + 0.5 * k * x_t[0]**2 + G * x_t[0]**4)

rho_t = [rho_0.copy()]
for i, t in enumerate(t_list[1:], 1):
    drho_dt = L @ rho_t[-1]

    # Simple Euler integration
    rho_t.append(rho_t[-1] + drho_dt * (t_list[1] - t_list[0]))

    x_t[i] = rho_t[-1].dot(x.dot(rho_t[-1]))
    v_t[i] = rho_t[-1].dot(px.dot(rho_t[-1])) / m
    E_t[i] = (0.5 * m * v_t[i]**2 + 0.5 * k * x_t[i]**2 + G * x_t[i]**4)

And we can finally visualize the evolution of the phase space density
$\rho(x, p, t)$ as a 2D plot animation:

In [5]:
from IPython.display import HTML
from matplotlib.animation import FuncAnimation

plt.rcParams.update({"font.size": 8})
fig, ax = plt.subplots(figsize=(4.6, 2.8))

fig.suptitle(r"Phase space density $\rho(x, p, t)$ evolution")

img = ax.pcolormesh(x_list, px_list, rho_t[0].reshape(N_x, N_px),
                    shading="gouraud", rasterized=True,
                    vmin=-0.3, vmax=0.3, cmap="PuOr")
ax.set_xlabel("Position $x$")
ax.set_ylabel("Momentum $p_x$")
ax.set_xlim(-5, 5)
ax.set_ylim(-5, 5)

def animate(i):
    img.set_array(rho_t[i])
    return img,

ani = FuncAnimation(fig, animate, frames=range(0, len(t_list), 2000), interval=100, blit=True)

plt.close(fig)
HTML(ani.to_jshtml())

Once 
 
 Loop 
 
 Reflect

Or can visualize the final phase space density $\rho(x, p, t)$ as a 2D
plot:

In [6]:
plt.rcParams.update({"font.size": 12})

In [7]:
fig, ax = plt.subplots()

fig.suptitle(r"Phase space density $\rho(x, p, t)$ evolution")

img = ax.pcolormesh(x_list, px_list, rho_t[-1].reshape(N_x, N_px), 
                    shading="gouraud", rasterized=True,
                    vmin=-0.3, vmax=0.3, cmap="PuOr")
ax.set_xlabel("Position $x$")
ax.set_ylabel("Momentum $p_x$")

# Show in Quarto
plt.savefig("_tmp_fig.svg")
plt.close(fig)
SVG("_tmp_fig.svg")